In [15]:
import numpy as np
import sympy as sp
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [16]:
def get_slope_line(m, x0, y0, x):
    """Returns the y-values of a line with slope m passing through (x0, y0) evaluated at x."""
    return m * (x - x0) + y0

In [17]:
#| label: legendre_u_to_f

# -- Precompute the "constant" data for U(S) --
S_fixed = np.linspace(0, 2, 100)
U_curve = 0.5 * S_fixed**2 + 1

# -- Create base figure with subplots --
fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=("U vs. S", "F vs. T"),
    horizontal_spacing=0.1
)

# --------------------------------------------------------
# 1) Left subplot: "U vs. S"
# --------------------------------------------------------
# (a) U(S) line – does NOT change with 's', so we add it once outside frames.
fig.add_trace(
    go.Scatter(
        x=S_fixed,
        y=U_curve,
        mode="lines",
        line=dict(color="blue"),
        showlegend=False
    ),
    row=1, col=1
)

# (b) A dashed horizontal line at U = 1
#    We do this using add_shape; it won’t change with frames.
# fig.add_shape(
#     type="line",
#     x0=0, x1=2,  # covers the same range as xlim
#     y0=1, y1=1,
#     line=dict(color="gray", dash="dash"),
#     xref="x1", yref="y1"
# )

# -- Prepare placeholders for the 4 dynamic traces on the left subplot
#    (we’ll update them inside frames for each new s):
#    1) Red point at (s, u)
#    2) Tangent line
#    3) Green point for the F-intercept on the y-axis
#    4) (Optional) We can place an annotation or just name the green point “F”.

# Red point (initially just a placeholder)
trace_red_point = go.Scatter(
    x=[],
    y=[],
    mode="markers",
    marker=dict(color="red", size=8),
    name="(s, U)",
    showlegend=False
)

# Tangent line
trace_tangent_line = go.Scatter(
    x=[],
    y=[],
    mode="lines",
    line=dict(color="orange"),
    name="Tangent line",
    showlegend=False
)

# Green intercept (F)
trace_green_intercept = go.Scatter(
    x=[],
    y=[],
    mode="markers+text",
    text=["F"],        # We can label this point “F”
    textposition="top center",
    marker=dict(color="green", size=8),
    name="F-intercept",
    showlegend=False
)

# Add these dynamic traces to the left subplot
fig.add_trace(trace_red_point, row=1, col=1)
fig.add_trace(trace_tangent_line, row=1, col=1)
fig.add_trace(trace_green_intercept, row=1, col=1)

# --------------------------------------------------------
# 2) Right subplot: "F vs. T"
# --------------------------------------------------------
# Similarly, we’ll have 2 dynamic traces on the right subplot:
#    1) Orange point (t, f)
#    2) F(T) line

trace_orange_point = go.Scatter(
    x=[],
    y=[],
    mode="markers",
    marker=dict(color="orange", size=8),
    name="(t, F)",
    showlegend=False
)

trace_F_line = go.Scatter(
    x=[],
    y=[],
    mode="lines",
    line=dict(color="green"),
    name="F(T)",
    showlegend=False
)

# Add these dynamic traces to the right subplot
fig.add_trace(trace_orange_point, row=1, col=2)
fig.add_trace(trace_F_line, row=1, col=2)

# --------------------------------------------------------
# Create frames for each s-value in a range
# --------------------------------------------------------
s_values = np.linspace(0, 2, 51, endpoint=True)

frames = []
for s in s_values:
    # Compute values needed
    # 1) For left subplot
    dUdS = s
    u = 0.5 * s**2 + 1
    xlim = (0, 2)

    # Slope line endpoints
    slope_endpt0 = (xlim[0], get_slope_line(dUdS, s, u, xlim[0]))
    slope_endpt1 = (xlim[1], get_slope_line(dUdS, s, u, xlim[1]))

    # 2) For right subplot
    t = dUdS
    f = u - dUdS * s  # F at that point
    T_line = np.linspace(xlim[0], t, 100)
    S_line = np.linspace(xlim[0], s, 100)
    F_line = 0.5 * S_line**2 + 1 - T_line * S_line

    # Build the data "updates" for each of our dynamic traces (in the same order they were added):
    #  - trace_red_point ->   [s], [u]
    #  - trace_tangent_line -> [x0, x1], [y0, y1]
    #  - trace_green_intercept -> [x0], [y0]
    #  - trace_orange_point -> [t], [f]
    #  - trace_F_line -> T_line, F_line

    frame_data = [
        go.Scatter(
            x=S_fixed,
            y=U_curve,
            mode="lines",
            line=dict(color="blue"),
        ),
        go.Scatter(x=[s], y=[u], mode="markers"),  # red point
        go.Scatter(x=[slope_endpt0[0], slope_endpt1[0]],
                   y=[slope_endpt0[1], slope_endpt1[1]], mode="lines"),  # tangent line
        go.Scatter(x=[slope_endpt0[0]], y=[slope_endpt0[1]], mode="markers+text", text=["F"]),  # green intercept
        go.Scatter(x=[t], y=[f], mode="markers"),  # orange point
        go.Scatter(x=T_line, y=F_line, mode="lines")  # F(T) line
    ]

    frames.append(
        go.Frame(
            data=frame_data,
            name=f"s={s:.2f}"
        )
    )

# --------------------------------------------------------
# Add frames to the figure
# --------------------------------------------------------
fig.frames = frames

# --------------------------------------------------------
# Create the slider
# --------------------------------------------------------
# We'll build one slider that goes over all s-values.
slider_steps = []
for i, s in enumerate(s_values):
    step = dict(
        method="animate",
        args=[
            [f"s={s:.2f}"],  # frame name
            dict(mode="immediate", frame=dict(duration=0, redraw=True), transition=dict(duration=0))
        ],
        label=f"{s:.2f}"
    )
    slider_steps.append(step)

sliders = [
    dict(
        active=0,
        currentvalue={"prefix": "s = "},
        pad={"t": 50},
        steps=slider_steps
    )
]

# --------------------------------------------------------
# Update figure layout and axis settings
# --------------------------------------------------------
fig.update_xaxes(
    range=[0, 2],
    title_text="S",
    title_font=dict(color="red"),
    row=1, col=1
)
fig.update_yaxes(
    range=[-2, 4],
    title_text="U",
    title_font=dict(color="blue"),
    row=1, col=1
)

fig.update_xaxes(
    range=[0, 2],
    title_text="T",
    title_font=dict(color="orange"),
    row=1, col=2
)
fig.update_yaxes(
    range=[-2, 4],
    title_text="F",
    title_font=dict(color="green"),
    row=1, col=2
)

fig.update_layout(
    width=700,
    height=500,
    showlegend=True,
    sliders=sliders,
    template="simple_white",
    # # Buttons to play/pause animation
    # updatemenus=[{
    #     "type": "buttons",
    #     "buttons": [
    #         {
    #             "label": "Play",
    #             "method": "animate",
    #             "args": [
    #                 None,
    #                 dict(
    #                     frame=dict(duration=300, redraw=True),
    #                     fromcurrent=True
    #                 )
    #             ]
    #         },
    #         {
    #             "label": "Pause",
    #             "method": "animate",
    #             "args": [
    #                 [None],
    #                 dict(frame=dict(duration=0, redraw=False), mode="immediate")
    #             ]
    #         }
    #     ],
    #     "pad": {"r": 10, "t": 70},
    #     "showactive": True,
    #     "x": 0.1,
    #     "xanchor": "right",
    #     "y": 0,
    #     "yanchor": "top"
    # }]
)

# --------------------------------------------------------
# Show the figure
# --------------------------------------------------------
fig.show()

In [18]:
#| label: legendre_3d

# --------------------------------------------------------------------------------
# 1) Define U(s,v) and partial derivatives
# --------------------------------------------------------------------------------
s_sym, v_sym = sp.symbols("s v", real=True)
a, b, c, offset = 0.01, 0.005, 150, 100

u_expr = a*s_sym**2 + b*(v_sym - c)**2 + offset
u_func = sp.lambdify((s_sym, v_sym), u_expr, 'numpy')

du_ds_expr = sp.diff(u_expr, s_sym)
du_dv_expr = sp.diff(u_expr, v_sym)
du_ds_func = sp.lambdify(s_sym, du_ds_expr, 'numpy')
du_dv_func = sp.lambdify(v_sym, du_dv_expr, 'numpy')

def tangent_plane_z(s0, v0, s_grid, v_grid):
    """
    z = U(s0, v0)
      + (dU/ds)(s0)*(s_grid - s0)
      + (dU/dv)(v0)*(v_grid - v0)
    """
    return (
        u_func(s0, v0)
        + du_ds_func(s0)*(s_grid - s0)
        + du_dv_func(v0)*(v_grid - v0)
    )

def tangent_z_at_point(s0, v0, x, y):
    """
    Tangent-plane Z value at point (x,y),
    given the tangent plane defined at (s0,v0).
    """
    return (
        u_func(s0, v0)
        + du_ds_func(s0)*(x - s0)
        + du_dv_func(v0)*(y - v0)
    )

# --------------------------------------------------------------------------------
# 2) Build the main U(s,v) surface on a grid
# --------------------------------------------------------------------------------
s_vals = np.linspace(0, 100, 50)
v_vals = np.linspace(0, 150, 50)
S, V = np.meshgrid(s_vals, v_vals)
U = u_func(S, V)

# --------------------------------------------------------------------------------
# 3) Single parameter t in [0,1]: s(t)=100*t, v(t)=150*t
# --------------------------------------------------------------------------------
t_init = 0.0
s_init = 100.0 * t_init
v_init = 150.0 * t_init

T_plane_init = tangent_plane_z(s_init, v_init, S, V)

# --------------------------------------------------------------------------------
# 4) Curves U(S)|_{v=v_init} and U(V)|_{s=s_init}
# --------------------------------------------------------------------------------
s_line = np.linspace(0, 100, 50)
U_S_line_z_init = u_func(s_line, v_init)
U_S_line_x_init = s_line
U_S_line_y_init = np.full_like(s_line, v_init)

v_line = np.linspace(0, 150, 50)
U_V_line_z_init = u_func(s_init, v_line)
U_V_line_x_init = np.full_like(v_line, s_init)
U_V_line_y_init = v_line

# --------------------------------------------------------------------------------
# 5) Tangent lines for F, H, G intercepts
# --------------------------------------------------------------------------------
def line_in_tangent_plane(s0, v0, x1, y1, steps=2):
    """
    Return arrays (x_arr, y_arr, z_arr) for a line in the tangent plane
    from (s0, v0) to (x1, y1).
    """
    t_arr = np.linspace(0, 1, steps)
    x_arr = s0 + t_arr*(x1 - s0)
    y_arr = v0 + t_arr*(y1 - v0)
    z_arr = [tangent_z_at_point(s0, v0, xx, yy) for xx, yy in zip(x_arr, y_arr)]
    return x_arr, y_arr, z_arr

# Lines at t_init
f_line_x_init, f_line_y_init, f_line_z_init = line_in_tangent_plane(s_init, v_init, 0, v_init)
h_line_x_init, h_line_y_init, h_line_z_init = line_in_tangent_plane(s_init, v_init, s_init, 0)
g_line_x_init, g_line_y_init, g_line_z_init = line_in_tangent_plane(s_init, v_init, 0, 0)

# Intercept markers at t_init:
f_marker_z_init = tangent_z_at_point(s_init, v_init, 0, v_init)
h_marker_z_init = tangent_z_at_point(s_init, v_init, s_init, 0)
g_marker_z_init = tangent_z_at_point(s_init, v_init, 0, 0)

# --------------------------------------------------------------------------------
# 6) Construct initial figure with multiple traces
# --------------------------------------------------------------------------------
# directed axis
cone_coords = np.array([
    [100, 0, 0],  # S axis
    [0, 150, 0],  # V axis
    [0, 0, 350],  # U axis
])
cone_vecs = np.array([
    [1, 0, 0],  # V axis
    [0, 1, 0],  # T axis
    [0, 0, 1],  # P axis
])

fig = go.Figure(
    data=[
        # (0) The 3D surface U(s,v)
        go.Surface(
            x=S,
            y=V,
            z=U,
            colorscale="Viridis",
            opacity=0.8,
            name="U(s,v)",
            showscale=False,
            showlegend=True
        ),
        # (1) The tangent plane
        go.Surface(
            x=S,
            y=V,
            z=T_plane_init,
            colorscale="gray",
            opacity=0.5,
            name="Tangent Plane",
            showscale=False,
            showlegend=True
        ),
        # (2) The point (s,v) on the surface
        go.Scatter3d(
            x=[s_init],
            y=[v_init],
            z=[u_func(s_init, v_init)],
            mode="markers+text",
            text=["U(S,V)"],
            marker=dict(size=5, color="red"),
            name="U(S,V)"
        ),
        # (3) U(S)|_{v=const} curve (red)
        go.Scatter3d(
            x=U_S_line_x_init,
            y=U_S_line_y_init,
            z=U_S_line_z_init,
            mode="lines",
            line=dict(color="red", width=5),
            name="U(S)|_{v=const}"
        ),
        # (4) U(V)|_{s=const} curve (blue)
        go.Scatter3d(
            x=U_V_line_x_init,
            y=U_V_line_y_init,
            z=U_V_line_z_init,
            mode="lines",
            line=dict(color="blue", width=5),
            name="U(V)|_{s=const}"
        ),
        # (5) F-line: from (s,v) to (0,v)
        go.Scatter3d(
            x=f_line_x_init,
            y=f_line_y_init,
            z=f_line_z_init,
            mode="lines+markers",
            line=dict(color="orange", width=4),
            marker=dict(size=2, color="orange"),
            name="F-line"
        ),
        # (6) H-line: from (s,v) to (s,0)
        go.Scatter3d(
            x=h_line_x_init,
            y=h_line_y_init,
            z=h_line_z_init,
            mode="lines",
            line=dict(color="magenta", width=4),
            # marker=dict(size=2, color="magenta"),
            name="H-line"
        ),
        # (7) G-line: from (s,v) to (0,0)
        go.Scatter3d(
            x=g_line_x_init,
            y=g_line_y_init,
            z=g_line_z_init,
            mode="lines",
            line=dict(color="green", width=4),
            # marker=dict(size=2, color="green"),
            name="G-line"
        ),
        # (8) F-marker at intercept (0,v)
        go.Scatter3d(
            x=[0],
            y=[v_init],
            z=[f_marker_z_init],
            mode="markers+text",
            text=["F(T,V)"],
            textposition="top center",
            textfont=dict(color="orange"),
            marker=dict(color="orange", size=5),
            name="F(T,V)"
        ),
        # (9) H-marker at intercept (s,0)
        go.Scatter3d(
            x=[s_init],
            y=[0],
            z=[h_marker_z_init],
            mode="markers+text",
            text=["H(S,P)"],
            textposition="top center",
            textfont=dict(color="magenta"),
            marker=dict(color="magenta", size=5),
            name="H(S,P)"
        ),
        # (10) G-marker at intercept (0,0)
        go.Scatter3d(
            x=[0],
            y=[0],
            z=[g_marker_z_init],
            mode="markers+text",
            text=["G(T,P)"],
            textposition="top center",
            textfont=dict(color="green"),
            marker=dict(color="green", size=5),
            name="G(T,P)"
        ),
        go.Cone(
            x=cone_coords[:, 0],
            y=cone_coords[:, 1],
            z=cone_coords[:, 2],
            u=cone_vecs[:, 0],
            v=cone_vecs[:, 1],
            w=cone_vecs[:, 2],
            showlegend=False,
            showscale=False,
            sizeref=0.05,
            colorscale=[[0, "black"], [1, "black"]],
            hoverinfo="skip"
        ),
        go.Scatter3d(
            x=[0, 100, None, 0, 0, None, 0, 0],
            y=[0, 0, None, 0, 150, None, 0, 0],
            z=[0, 0, None, 0, 0, None, 0, 350],
            mode="lines",
            line=dict(
                    color="black",
                width=5
            ),
            showlegend=False,
            hoverinfo="skip"),
    ],
    layout=go.Layout(
        title=f"s={s_init:.1f}, v={v_init:.1f}",
        scene=dict(
            xaxis_title='S',
            yaxis_title='V',
            zaxis_title='U',
            xaxis=dict(range=[0, 100], autorange=False, showticklabels=False,
                       showbackground=False, showgrid=False, ticks="",
                       showline=False, zeroline=False),
            yaxis=dict(range=[0, 150], autorange=False, showticklabels=False,
                       showbackground=False, showgrid=False, ticks="",
                       showline=False, zeroline=False),
            zaxis=dict(range=[0, 350], autorange=False, showticklabels=False,
                       showbackground=False, showgrid=False, ticks="",
                       showline=False, zeroline=False),
            aspectmode="cube"
        ),
        scene_camera=dict(
            eye=dict(x=-0.35, y=-1.75, z=0.45),
            projection=dict(
                type="orthographic"
            )
        ),
    )
)

# --------------------------------------------------------------------------------
# 7) Build the slider steps
# --------------------------------------------------------------------------------
slider_steps = []
n_steps = 11

for i in range(n_steps):
    t = i/(n_steps - 1)  # from 0..1
    s_val = 100.0 * t
    v_val = 150.0 * t

    # (a) Tangent plane
    T_plane = tangent_plane_z(s_val, v_val, S, V)

    # (b) The point on surface
    point_z = [u_func(s_val, v_val)]

    # (c) The 1D slices
    U_S_line_z = u_func(s_line, v_val)
    U_S_line_x = s_line
    U_S_line_y = np.full_like(s_line, v_val)

    U_V_line_z = u_func(s_val, v_line)
    U_V_line_x = np.full_like(v_line, s_val)
    U_V_line_y = v_line

    # (d) Tangent lines
    f_line_x, f_line_y, f_line_z = line_in_tangent_plane(s_val, v_val, 0, v_val)
    h_line_x, h_line_y, h_line_z = line_in_tangent_plane(s_val, v_val, s_val, 0)
    g_line_x, g_line_y, g_line_z = line_in_tangent_plane(s_val, v_val, 0, 0)

    # (e) F, H, G intercept markers
    f_marker_z = [tangent_z_at_point(s_val, v_val, 0, v_val)]
    h_marker_z = [tangent_z_at_point(s_val, v_val, s_val, 0)]
    g_marker_z = [tangent_z_at_point(s_val, v_val, 0, 0)]

    step = dict(
        method="update",
        args=[
            # First dict: updating the data for all 11 traces
            {
                "z": [
                    U,                # (0) main surface
                    T_plane,          # (1) tangent plane
                    point_z,          # (2) the point
                    U_S_line_z,       # (3) U(S)
                    U_V_line_z,       # (4) U(V)
                    f_line_z,         # (5) F-line
                    h_line_z,         # (6) H-line
                    g_line_z,         # (7) G-line
                    f_marker_z,       # (8) F-marker
                    h_marker_z,       # (9) H-marker
                    g_marker_z,        # (10) G-marker
                    None,
                    [0, 0, None, 0, 0, None, 0, 350],
                ],
                "x": [
                    S,                # (0) main surface
                    S,                # (1) tangent plane
                    [s_val],          # (2) the point
                    U_S_line_x,       # (3) U(S)
                    U_V_line_x,       # (4) U(V)
                    f_line_x,         # (5) F-line
                    h_line_x,         # (6) H-line
                    g_line_x,         # (7) G-line
                    [0],              # (8) F-marker x
                    [s_val],          # (9) H-marker x
                    [0],              # (10) G-marker x,
                    None,
                    [0, 100, None, 0, 0, None, 0, 0],
                ],
                "y": [
                    V,                # (0) main surface
                    V,                # (1) tangent plane
                    [v_val],          # (2) the point
                    U_S_line_y,       # (3) U(S)
                    U_V_line_y,       # (4) U(V)
                    f_line_y,         # (5) F-line
                    h_line_y,         # (6) H-line
                    g_line_y,         # (7) G-line
                    [v_val],          # (8) F-marker y
                    [0],              # (9) H-marker y
                    [0],              # (10) G-marker y
                    None,
                    [0, 0, None, 0, 150, None, 0, 0],
                ],
            },
            # Second dict: layout updates (title, etc.)
            {
                "title": f"s={s_val:.1f}, v={v_val:.1f}"
            }
        ],
        label=f"t={t:.1f}"
    )
    slider_steps.append(step)

single_slider = dict(
    active=0,
    pad={"t": 20},
    currentvalue={"prefix": "t: "},
    steps=slider_steps
)

fig.update_layout(sliders=[single_slider], template="simple_white")
fig.show()
